In [1]:
from __future__ import print_function, division
import torch
import torch
import torch.nn as nn
import torch.optim as optim
import data as dt
import model_4_o as md
import copy
from pytorch_ssim import ssim
from torch.utils.data import DataLoader
import os
import matplotlib.pyplot as plt
from torchvision import transforms, utils
# e/d + i
# best mode so far

In [2]:
# Load model
cwd = os.getcwd();
path = os.path.join(cwd, 'Saved model', 'encoderresinfo.pth')
model = md.Net()
model.load_state_dict(torch.load(path))
model.eval()

Net(
  (block0): Sequential(
    (0): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3))
    (1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (2): LeakyReLU(negative_slope=0.1)
  )
  (block1): Sequential(
    (0): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (2): LeakyReLU(negative_slope=0.1)
    (3): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (4): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (5): LeakyReLU(negative_slope=0.1)
  )
  (info1): Sequential(
    (0): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (2): LeakyReLU(negative_slope=0.1)
  )
  (block2): Sequential(
    (0): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
  

In [3]:
# print gpu
torch.cuda.set_device(0)
currentDevice = torch.cuda.current_device()
print("Current GPU: " + str(currentDevice))
print(str(torch.cuda.device_count()))
print(str(torch.cuda.get_device_capability(currentDevice)))
print(torch.__version__)

Current GPU: 0
8
(7, 0)
1.0.0


In [4]:
USE_GPU = 1
if USE_GPU and torch.cuda.is_available():
    device = torch.device('cuda:0')
else:
    device = "cpu"
print(device)

cuda:0


In [ ]:
CSVFILE = 0
# generate csv file, run only for the first time
if CSVFILE:
    dt.generate_csv()
# dt.generate_csv()

In [5]:
csvFilePath = dt.get_csv_path()
transformed_dataset = dt.HE_SHG_Dataset(csv_file=csvFilePath,
                                               transform=dt.Compose([                                              
                                               dt.Rescale(96),                                     
                                               dt.Normalize(),
                                               dt.ToTensor()
                                           ]))
# TODO: change the normalization parameters

In [6]:
# batchsize 1200
dataloader = DataLoader(transformed_dataset, batch_size=32,
                        shuffle=True, num_workers=0)

In [ ]:
dt.show_patch(dataloader) 

In [7]:
# declare MSE loss here
criterionMSE = nn.MSELoss()
criterionMSE = criterionMSE.cuda()
optimizer = optim.Adam(model.parameters(), lr=0.01)

In [8]:
def train(epoch, p, windowsize):
    epoch_loss = 0
    for iteration, batch in enumerate(dataloader):
        input, target = batch['input'].to(device), batch['output'].to(device)

        optimizer.zero_grad()
        output = model(input)
        targetf = target.float()
        targetf = targetf[:, None]
        
        lossMSE = criterionMSE(output, targetf)      
        lossSSIM = 1-ssim(output, targetf, window_size=windowsize)
        
        # 0.75->0.4 after 3 epochs
        loss = p*lossMSE + (1-p)*lossSSIM
        combineLoss = p*lossMSE.item() + (1-p)*lossSSIM.item()
        
        epoch_loss = epoch_loss + combineLoss
        loss.backward()
        optimizer.step()
    
        if iteration%50 == 0:
            print("lossMSE: " + str(lossMSE.item()) +
                  " " + "lossSSIM: " + str(lossSSIM.item()))
            print("===> Epoch[{}]({}/{}): Loss: {:.4f}".format(epoch, iteration, len(dataloader), loss.item()))

    print("===> Epoch {} Complete: Avg. Loss: {:.4f}".format(epoch, epoch_loss / len(dataloader)))


In [9]:
def test():
    avg_psnr = 0
    with torch.no_grad():
        for iteration, batch in enumerate(dataloader):
            input, target = batch['input'].to(device), batch['output'].to(device)
                
            prediction = model(input)

            target = target.float()

            outdataloader = {'input':prediction,'output':target}
            
            print(outdataloader['input'].size(), 
                      outdataloader['output'].size())

            plt.figure()
            input_batch, label_batch = outdataloader['input'], outdataloader['output']
            batch_size = 32
            im_size = input_batch.size(2)
            label_batch=label_batch.reshape([batch_size,1,im_size,im_size])
            print(label_batch.size())
#             for img in input_batch:
#                 for t, m, s in zip(img, [0.5, 0.5, 0.5], [0.5, 0.5, 0.5]):
#                     t.mul_(s).add_(m)
                            
#             for img in label_batch:
#                 for t, m, s in zip(img, [0.5, 0.5, 0.5], [0.5, 0.5, 0.5]):
#                     t.mul_(s).add_(m)                           
            grid = utils.make_grid(input).cpu()
            plt.imshow(grid.numpy().transpose((1, 2, 0)))
            plt.figure()
    
            grid = utils.make_grid(input_batch).cpu()
            plt.imshow(grid.numpy().transpose((1, 2, 0)))
            plt.figure()

            grid = utils.make_grid(label_batch).cpu()
            plt.imshow(grid.numpy().transpose((1, 2, 0)))

            plt.axis('off')
            plt.ioff()
            plt.show()
            
            targetf = target[:, None]
            
            lossMSE = criterionMSE(prediction, targetf)      
            lossSSIM = -ssim(prediction, targetf)
        
            p = 0.25
            loss = p*lossMSE + (1-p)*lossSSIM
            combineLoss = p*lossMSE.item() + (1-p)*lossSSIM.item()
#             mse = criterion(prediction, target.float())

            psnr = 10 * torch.log10(1 / loss)
            avg_psnr += psnr
            if iteration == 16:
                break
    print("===> Avg. PSNR: {:.4f} dB".format(avg_psnr / len(dataloader)))

In [ ]:
SAVE = 0
if SAVE:
    cwd = os.getcwd();
    path = os.path.join(cwd, 'Saved model', 'encoderresinfo.pth')
    torch.save(model.state_dict(), path)

In [ ]:
# choose GPU and load model to GPU
gpu_ids = [1, 2, 3, 4, 5, 6]
torch.cuda.set_device(gpu_ids[0])
model = torch.nn.DataParallel(model, device_ids=gpu_ids)
model.cuda()

In [ ]:
model.to(device)
l = 0.01
p = 0
windowsize = 16
for epoch in range(1, 200 + 1):
    if epoch%5 == 0:
        windowsize = windowsize+1
        p = p*1
        l = l*0.95
        if windowsize >= 16:
            windowsze = 16
    optimizer = optim.Adam(model.parameters(), lr=l)
        
    train(epoch, p, windowsize)

lossMSE: 0.003795218886807561 lossSSIM: 0.23527216911315918
===> Epoch[1](0/25343): Loss: 0.2353
lossMSE: 0.0034746204037219286 lossSSIM: 0.2395954728126526
===> Epoch[1](50/25343): Loss: 0.2396
lossMSE: 0.005337276495993137 lossSSIM: 0.37588900327682495
===> Epoch[1](100/25343): Loss: 0.3759
lossMSE: 0.00580750172957778 lossSSIM: 0.25722736120224
===> Epoch[1](150/25343): Loss: 0.2572
lossMSE: 0.003364729695022106 lossSSIM: 0.2693172097206116
===> Epoch[1](200/25343): Loss: 0.2693
lossMSE: 0.005230859387665987 lossSSIM: 0.24197548627853394
===> Epoch[1](250/25343): Loss: 0.2420
lossMSE: 0.006105458363890648 lossSSIM: 0.302550733089447
===> Epoch[1](300/25343): Loss: 0.3026
lossMSE: 0.008685322478413582 lossSSIM: 0.3064940571784973
===> Epoch[1](350/25343): Loss: 0.3065
lossMSE: 0.005391164682805538 lossSSIM: 0.30530381202697754
===> Epoch[1](400/25343): Loss: 0.3053
lossMSE: 0.006050083786249161 lossSSIM: 0.3122648000717163
===> Epoch[1](450/25343): Loss: 0.3123
lossMSE: 0.00685601308

lossMSE: 0.0013323359889909625 lossSSIM: 0.174993097782135
===> Epoch[1](4150/25343): Loss: 0.1750
lossMSE: 0.005398801527917385 lossSSIM: 0.2711421847343445
===> Epoch[1](4200/25343): Loss: 0.2711
lossMSE: 0.007371341343969107 lossSSIM: 0.32641690969467163
===> Epoch[1](4250/25343): Loss: 0.3264
lossMSE: 0.010562816634774208 lossSSIM: 0.3207828402519226
===> Epoch[1](4300/25343): Loss: 0.3208
lossMSE: 0.0038017970509827137 lossSSIM: 0.2654470205307007
===> Epoch[1](4350/25343): Loss: 0.2654
lossMSE: 0.003838097909465432 lossSSIM: 0.289883553981781
===> Epoch[1](4400/25343): Loss: 0.2899
lossMSE: 0.004177100490778685 lossSSIM: 0.28378826379776
===> Epoch[1](4450/25343): Loss: 0.2838
lossMSE: 0.004667340777814388 lossSSIM: 0.26966673135757446
===> Epoch[1](4500/25343): Loss: 0.2697
lossMSE: 0.005759344436228275 lossSSIM: 0.2981148958206177
===> Epoch[1](4550/25343): Loss: 0.2981
lossMSE: 0.007508253213018179 lossSSIM: 0.3106200098991394
===> Epoch[1](4600/25343): Loss: 0.3106
lossMSE: 0

lossMSE: 0.011174162849783897 lossSSIM: 0.3023800849914551
===> Epoch[1](8300/25343): Loss: 0.3024
lossMSE: 0.004782581236213446 lossSSIM: 0.27064239978790283
===> Epoch[1](8350/25343): Loss: 0.2706
lossMSE: 0.0035644115414470434 lossSSIM: 0.29262685775756836
===> Epoch[1](8400/25343): Loss: 0.2926
lossMSE: 0.0027268542908132076 lossSSIM: 0.2136244773864746
===> Epoch[1](8450/25343): Loss: 0.2136
lossMSE: 0.00994249526411295 lossSSIM: 0.26610320806503296
===> Epoch[1](8500/25343): Loss: 0.2661
lossMSE: 0.010497679002583027 lossSSIM: 0.27487850189208984
===> Epoch[1](8550/25343): Loss: 0.2749
lossMSE: 0.009875316172838211 lossSSIM: 0.2745007276535034
===> Epoch[1](8600/25343): Loss: 0.2745
lossMSE: 0.0031674699857831 lossSSIM: 0.2558705806732178
===> Epoch[1](8650/25343): Loss: 0.2559
lossMSE: 0.008763275109231472 lossSSIM: 0.2662305235862732
===> Epoch[1](8700/25343): Loss: 0.2662
lossMSE: 0.010085110552608967 lossSSIM: 0.2849370837211609
===> Epoch[1](8750/25343): Loss: 0.2849
lossMSE

lossMSE: 0.006917132064700127 lossSSIM: 0.28665560483932495
===> Epoch[1](12400/25343): Loss: 0.2867
lossMSE: 0.003696391126140952 lossSSIM: 0.2981802225112915
===> Epoch[1](12450/25343): Loss: 0.2982
lossMSE: 0.006534097716212273 lossSSIM: 0.2981315851211548
===> Epoch[1](12500/25343): Loss: 0.2981
lossMSE: 0.007227682508528233 lossSSIM: 0.24306046962738037
===> Epoch[1](12550/25343): Loss: 0.2431
lossMSE: 0.010244706645607948 lossSSIM: 0.3180691599845886
===> Epoch[1](12600/25343): Loss: 0.3181
lossMSE: 0.007208121940493584 lossSSIM: 0.250571608543396
===> Epoch[1](12650/25343): Loss: 0.2506
lossMSE: 0.010283863171935081 lossSSIM: 0.33724749088287354
===> Epoch[1](12700/25343): Loss: 0.3372
lossMSE: 0.0034283865243196487 lossSSIM: 0.22425252199172974
===> Epoch[1](12750/25343): Loss: 0.2243
lossMSE: 0.00820926483720541 lossSSIM: 0.19872039556503296
===> Epoch[1](12800/25343): Loss: 0.1987
lossMSE: 0.00685702171176672 lossSSIM: 0.27114230394363403
===> Epoch[1](12850/25343): Loss: 0.2

lossMSE: 0.012458649463951588 lossSSIM: 0.39292508363723755
===> Epoch[1](16500/25343): Loss: 0.3929
lossMSE: 0.003017514944076538 lossSSIM: 0.224432110786438
===> Epoch[1](16550/25343): Loss: 0.2244
lossMSE: 0.0021067336201667786 lossSSIM: 0.22217869758605957
===> Epoch[1](16600/25343): Loss: 0.2222
lossMSE: 0.006263796705752611 lossSSIM: 0.2905658483505249
===> Epoch[1](16650/25343): Loss: 0.2906
lossMSE: 0.012262308970093727 lossSSIM: 0.3049774765968323
===> Epoch[1](16700/25343): Loss: 0.3050
lossMSE: 0.003790598828345537 lossSSIM: 0.21694010496139526
===> Epoch[1](16750/25343): Loss: 0.2169
lossMSE: 0.008462782949209213 lossSSIM: 0.3320164084434509
===> Epoch[1](16800/25343): Loss: 0.3320
lossMSE: 0.010600373148918152 lossSSIM: 0.2958414554595947
===> Epoch[1](16850/25343): Loss: 0.2958
lossMSE: 0.008061017841100693 lossSSIM: 0.25285184383392334
===> Epoch[1](16900/25343): Loss: 0.2529
lossMSE: 0.004542926326394081 lossSSIM: 0.26413583755493164
===> Epoch[1](16950/25343): Loss: 0.

...

lossMSE: 0.007945899851620197 lossSSIM: 0.28479552268981934
===> Epoch[71](22750/25343): Loss: 0.2848
lossMSE: 0.005512250121682882 lossSSIM: 0.22590744495391846
===> Epoch[71](22800/25343): Loss: 0.2259
lossMSE: 0.010730864480137825 lossSSIM: 0.29279178380966187
===> Epoch[71](22850/25343): Loss: 0.2928
lossMSE: 0.002315081423148513 lossSSIM: 0.2163630723953247
===> Epoch[71](22900/25343): Loss: 0.2164
lossMSE: 0.007288302760571241 lossSSIM: 0.2783067226409912
===> Epoch[71](22950/25343): Loss: 0.2783
lossMSE: 0.005613481160253286 lossSSIM: 0.25085484981536865
===> Epoch[71](23000/25343): Loss: 0.2509
lossMSE: 0.0029696719720959663 lossSSIM: 0.19045764207839966
===> Epoch[71](23050/25343): Loss: 0.1905
lossMSE: 0.006353359203785658 lossSSIM: 0.2509044408798218
===> Epoch[71](23100/25343): Loss: 0.2509
lossMSE: 0.0033903224393725395 lossSSIM: 0.22721701860427856
===> Epoch[71](23150/25343): Loss: 0.2272
lossMSE: 0.006014873739331961 lossSSIM: 0.2611237168312073
===> Epoch[71](23200/253

lossMSE: 0.006212857086211443 lossSSIM: 0.2146429419517517
===> Epoch[72](1450/25343): Loss: 0.2146
lossMSE: 0.012633800506591797 lossSSIM: 0.264393150806427
===> Epoch[72](1500/25343): Loss: 0.2644
lossMSE: 0.009873483330011368 lossSSIM: 0.2202957272529602
===> Epoch[72](1550/25343): Loss: 0.2203
lossMSE: 0.009742051362991333 lossSSIM: 0.2712562680244446
===> Epoch[72](1600/25343): Loss: 0.2713
lossMSE: 0.0065770638175308704 lossSSIM: 0.25190460681915283
===> Epoch[72](1650/25343): Loss: 0.2519
lossMSE: 0.0065418872982263565 lossSSIM: 0.2566233277320862
===> Epoch[72](1700/25343): Loss: 0.2566
lossMSE: 0.005421323701739311 lossSSIM: 0.2608208656311035
===> Epoch[72](1750/25343): Loss: 0.2608
lossMSE: 0.004470003768801689 lossSSIM: 0.24023306369781494
===> Epoch[72](1800/25343): Loss: 0.2402
lossMSE: 0.005765337962657213 lossSSIM: 0.2871381640434265
===> Epoch[72](1850/25343): Loss: 0.2871
lossMSE: 0.001523691462352872 lossSSIM: 0.18944096565246582
===> Epoch[72](1900/25343): Loss: 0.1

lossMSE: 0.006461522541940212 lossSSIM: 0.2624092102050781
===> Epoch[72](5550/25343): Loss: 0.2624
lossMSE: 0.004703248851001263 lossSSIM: 0.30484700202941895
===> Epoch[72](5600/25343): Loss: 0.3048
lossMSE: 0.0064716096967458725 lossSSIM: 0.2579919695854187
===> Epoch[72](5650/25343): Loss: 0.2580
lossMSE: 0.009902315214276314 lossSSIM: 0.3166923522949219
===> Epoch[72](5700/25343): Loss: 0.3167
lossMSE: 0.010424246080219746 lossSSIM: 0.24098658561706543
===> Epoch[72](5750/25343): Loss: 0.2410
lossMSE: 0.0020041533280164003 lossSSIM: 0.21379870176315308
===> Epoch[72](5800/25343): Loss: 0.2138
lossMSE: 0.005079218652099371 lossSSIM: 0.27716416120529175
===> Epoch[72](5850/25343): Loss: 0.2772
lossMSE: 0.01462144311517477 lossSSIM: 0.3062182664871216
===> Epoch[72](5900/25343): Loss: 0.3062
lossMSE: 0.008372228592634201 lossSSIM: 0.30647027492523193
===> Epoch[72](5950/25343): Loss: 0.3065
lossMSE: 0.009587017819285393 lossSSIM: 0.25644487142562866
===> Epoch[72](6000/25343): Loss: 

lossMSE: 0.007831808179616928 lossSSIM: 0.27200794219970703
===> Epoch[72](9650/25343): Loss: 0.2720
lossMSE: 0.002558646025136113 lossSSIM: 0.1766110062599182
===> Epoch[72](9700/25343): Loss: 0.1766
lossMSE: 0.0022890360560268164 lossSSIM: 0.1427251100540161
===> Epoch[72](9750/25343): Loss: 0.1427
lossMSE: 0.009939862415194511 lossSSIM: 0.331339955329895
===> Epoch[72](9800/25343): Loss: 0.3313
lossMSE: 0.0053934683091938496 lossSSIM: 0.24207520484924316
===> Epoch[72](9850/25343): Loss: 0.2421
lossMSE: 0.006601812317967415 lossSSIM: 0.3037400245666504
===> Epoch[72](9900/25343): Loss: 0.3037
lossMSE: 0.0026788408868014812 lossSSIM: 0.21472054719924927
===> Epoch[72](9950/25343): Loss: 0.2147
lossMSE: 0.007790868636220694 lossSSIM: 0.29011356830596924
===> Epoch[72](10000/25343): Loss: 0.2901
lossMSE: 0.008866345509886742 lossSSIM: 0.27738314867019653
===> Epoch[72](10050/25343): Loss: 0.2774
lossMSE: 0.0034301637206226587 lossSSIM: 0.24703586101531982
===> Epoch[72](10100/25343): L

lossMSE: 0.008476290851831436 lossSSIM: 0.2897205948829651
===> Epoch[72](13700/25343): Loss: 0.2897
lossMSE: 0.009506459347903728 lossSSIM: 0.30275148153305054
===> Epoch[72](13750/25343): Loss: 0.3028
lossMSE: 0.008271605707705021 lossSSIM: 0.2794345021247864
===> Epoch[72](13800/25343): Loss: 0.2794
lossMSE: 0.005426887888461351 lossSSIM: 0.27676159143447876
===> Epoch[72](13850/25343): Loss: 0.2768
lossMSE: 0.005922563374042511 lossSSIM: 0.2777222990989685
===> Epoch[72](13900/25343): Loss: 0.2777
lossMSE: 0.011121300980448723 lossSSIM: 0.3104866147041321
===> Epoch[72](13950/25343): Loss: 0.3105
lossMSE: 0.0061559234745800495 lossSSIM: 0.26778721809387207
===> Epoch[72](14000/25343): Loss: 0.2678
lossMSE: 0.003555052448064089 lossSSIM: 0.30802375078201294
===> Epoch[72](14050/25343): Loss: 0.3080
lossMSE: 0.008410349488258362 lossSSIM: 0.22577232122421265
===> Epoch[72](14100/25343): Loss: 0.2258
lossMSE: 0.007315999828279018 lossSSIM: 0.27568745613098145
===> Epoch[72](14150/2534